In [ ]:
import pandas as pd
import os
import numpy as np
from PIL import Image 
from tqdm import tqdm
import cv2
from mtcnn.mtcnn import MTCNN
import math

In [77]:
#crooping the face region
def crop_image(img):
    detector1 = MTCNN() 
   # pic = Image.open(img)
    img = np.array(img)
    img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)

    # detect faces in the image
    faces1 = detector1.detect_faces(img_rgb)

    faces=[]
    faces=np.array(faces)
    #MTCNN
    for result in faces1:
        x, y, w, h = result['box']
        x1, y1 = x + w, y + h

        faces = img_rgb[y:y+h, x:x+w]
        

    print(faces.shape)


    ######
    if len(faces)==0:

        img = Image.fromarray(img)
    else:    

        img = Image.fromarray(faces)
    im =np.array(img)
    return im

In [60]:
# alignment using the distance of eyes location
def euclidean_distance(v1, v2):
    return np.sqrt(np.sum((v1 - v2) ** 2))    

def alignment_procedure(img, left_eye, right_eye):
    #this function aligns given face in img based on left and right eye coordinates
    
    left_eye_x = left_eye[:,0]
 
    left_eye_x, left_eye_y = left_eye
    right_eye_x, right_eye_y = right_eye
 
    #-----------------------
    #find rotation direction
 
    if left_eye_y > right_eye_y:
        point_3rd = (right_eye_x, left_eye_y)
        direction = -1 #rotate same direction to clock
    else:
        point_3rd = (left_eye_x, right_eye_y)
        direction = 1 #rotate inverse direction of clock
 
    #-----------------------
    #find length of triangle edges
 
    a = euclidean_distance(np.array(left_eye), np.array(point_3rd))
    b = euclidean_distance(np.array(right_eye), np.array(point_3rd))
    c = euclidean_distance(np.array(right_eye), np.array(left_eye))
 
    #-----------------------
 
    #apply cosine rule
 
    if b != 0 and c != 0: #this multiplication causes division by zero in cos_a calculation
        cos_a = (b*b + c*c - a*a)/(2*b*c)
        angle = np.arccos(cos_a) #angle in radian
        angle = (angle * 180) / math.pi #radian to degree
 
    #-----------------------
    #rotate base image
 
    if direction == -1:
        angle = 90 - angle
 
    img = Image.fromarray(img)
    img = np.array(img.rotate(direction * angle))
 
    #-----------------------
 
    return img #return img anyway

# define a function for horizontally  
# concatenating images of different 
# heights  
def hconcat_resize(img_list,size,interpolation= cv2.INTER_CUBIC): 
      # take minimum hights 
    h, w = size 
      
    # image resizing  
    im_list_resize = [cv2.resize(img,(h,w)) for img in img_list] 
      
    # return final image 
    return cv2.hconcat(im_list_resize) 

In [84]:
def face_align(img,leye,reye,desiredFaceWidth,desiredFaceHeight):
    #img_shape=(img.shape[:2])
    desiredLeftEye=(0.35, 0.35)
    #print(img_shape)
    print(leye,reye)
    dY = reye[1] - leye[1]
    dX = reye[0] - leye[0]
    angle = np.degrees(np.arctan2(dY, dX)) - 180
    print(angle)
    # compute the desired right eye x-coordinate based on the
    # desired x-coordinate of the left eye
    desiredRightEyeX = 1.0 - desiredLeftEye[0]
    
    # determine the scale of the new resulting image by taking
    # the ratio of the distance between eyes in the *current*
    # image to the ratio of distance between eyes in the
    # *desired* image
    
    
    dist = np.sqrt((dX ** 2) + (dY ** 2))
    desiredDist = (desiredRightEyeX - desiredLeftEye[0])
    desiredDist *= desiredFaceWidth
    scale = desiredDist / dist
    print(dist)
    print(scale)
    # compute center (x, y)-coordinates (i.e., the median point)
    # between the two eyes in the input image
    eyesCenter = ((leye[0] + reye[0]) // 2,
                  (leye[1] + reye[1]) // 2)
    
    print(eyesCenter)
    # grab the rotation matrix for rotating and scaling the face
    M = cv2.getRotationMatrix2D(eyesCenter, angle, -scale)
    #M = cv2.getRotationMatrix2D(eyesCenter, angle, .5)
    # update the translation component of the matrix
    tX = desiredFaceWidth * 0.5
    tY = desiredFaceHeight * desiredLeftEye[1]
    M[0, 2] += (tX - eyesCenter[0])
    M[1, 2] += (tY - eyesCenter[1])
    
    # apply the affine transformation
    (w, h) = (desiredFaceWidth,desiredFaceHeight)
    output = cv2.warpAffine(img, M, (w, h),flags=cv2.INTER_CUBIC)
    #return the aligned face
    return output
    #return img

In [ ]:
#this part used for testing the figures
a = crop_image('/storage/ali/FER/JAFFE/jaffe/0anger/KA.AN1.39.tiff')

In [ ]:
#visualization the implementation test
import matplotlib.pyplot as plt
plt.imshow(a, cmap = "gray")

In [ ]:
#Local binary pattern implementation
import cv2
import numpy as np
from matplotlib import pyplot as plt
  
     
def get_pixel(img, center, x, y):
     
    new_value = 0
     
    try:
        # If local neighbourhood pixel
        # value is greater than or equal
        # to center pixel values then
        # set it to 1
        if img[x][y] >= center:
            new_value = 1
             
    except:
        # Exception is required when
        # neighbourhood value of a center
        # pixel value is null i.e. values
        # present at boundaries.
        pass
     
    return new_value
  
# Function for calculating LBP
def lbp_calculated_pixel(img, x, y):
  
    center = img[x][y]
  
    val_ar = []
     
    # top_left
    val_ar.append(get_pixel(img, center, x-1, y-1))
     
    # top
    val_ar.append(get_pixel(img, center, x-1, y))
     
    # top_right
    val_ar.append(get_pixel(img, center, x-1, y + 1))
     
    # right
    val_ar.append(get_pixel(img, center, x, y + 1))
     
    # bottom_right
    val_ar.append(get_pixel(img, center, x + 1, y + 1))
     
    # bottom
    val_ar.append(get_pixel(img, center, x + 1, y))
     
    # bottom_left
    val_ar.append(get_pixel(img, center, x + 1, y-1))
     
    # left
    val_ar.append(get_pixel(img, center, x, y-1))
      
    # Now, we need to convert binary
    # values to decimal
    power_val = [1, 2, 4, 8, 16, 32, 64, 128]
  
    val = 0
     
    for i in range(len(val_ar)):
        val += val_ar[i] * power_val[i]
         
    return val

in the below we take the figures from a folder and after processing such as cropping and alignment and or lbp transformation we saved them in new directory 

In [93]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/0angry'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                           | 0/958 [00:00<?, ?it/s]

1/1 [==============================] - 0s 9ms/step


  0%|                                                                                   | 1/958 [00:00<02:03,  7.73it/s]

(19, 18) (32, 16)
-188.7461622625552
13.152946437965905
6.8425732914273505
(25, 17)
1/1 [==============================] - 0s 12ms/step


...

100%|████████████████████████████████████████████████████████████████████████████████▋| 955/958 [01:30<00:00, 11.07it/s]

(15, 20) (28, 20)
-180.0
13.0
6.923076923076924
(21, 20)
1/1 [==============================] - 0s 9ms/step
(15, 17) (31, 18)
-176.42366562500266
16.0312195418814
5.6140457539662485
(23, 17)
1/1 [==============================] - 0s 9ms/step
(19, 20) (32, 23)
-167.0053832080835
13.341664064126334
6.745785200962754
(25, 21)


100%|████████████████████████████████████████████████████████████████████████████████▉| 957/958 [01:31<00:00, 10.73it/s]

1/1 [==============================] - 0s 9ms/step


100%|█████████████████████████████████████████████████████████████████████████████████| 958/958 [01:31<00:00, 10.50it/s]


In [94]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/1disgust'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                           | 0/111 [00:00<?, ?it/s]

1/1 [==============================] - 0s 8ms/step


  1%|▋                                                                                  | 1/111 [00:00<00:14,  7.42it/s]

(14, 18) (32, 18)
-180.0
18.0
5.000000000000001
(23, 18)
1/1 [==============================] - 0s 8ms/step


...

 96%|██████████████████████████████████████████████████████████████████████████████   | 107/111 [00:09<00:00, 11.60it/s]

(12, 15) (34, 17)
-174.80557109226518
22.090722034374522
4.074108571913334
(23, 16)
1/1 [==============================] - 0s 8ms/step
(15, 19) (31, 17)
-187.1250163489018
16.1245154965971
5.581563056514382
(23, 18)
1/1 [==============================] - 0s 8ms/step
(15, 19) (31, 18)
-183.57633437499734
16.0312195418814
5.6140457539662485
(23, 18)


 98%|███████████████████████████████████████████████████████████████████████████████▌ | 109/111 [00:09<00:00, 11.42it/s]

1/1 [==============================] - 0s 8ms/step
(24, 19) (38, 21)
-171.86989764584402
14.142135623730951
6.3639610306789285
(31, 20)
1/1 [==============================] - 0s 7ms/step
(9, 12) (29, 13)
-177.13759477388825
20.024984394500787
4.494385524950301
(19, 12)


100%|█████████████████████████████████████████████████████████████████████████████████| 111/111 [00:09<00:00, 11.17it/s]


In [52]:
img5 = cv2.imread('/storage/ali/FER/FER_code/aligned/1disgust/Training_1070239.jpg')
img6 = cv2.imread('/storage/ali/FER/FER_code/Cropped/1disgust/Training_1070239.jpg')
dif = img5.flatten()-img6.flatten()
print(np.sum(img5))

1180320


In [95]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/2fear'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                          | 0/1024 [00:00<?, ?it/s]

1/1 [==============================] - 0s 8ms/step


  0%|                                                                                  | 1/1024 [00:00<02:15,  7.53it/s]

(14, 20) (34, 20)
-180.0
20.0
4.500000000000001
(24, 20)
1/1 [==============================] - 0s 7ms/step
(11, 17) (23, 15)
-189.46232220802563
12.165525060596439
7.3979544287410794
(17, 16)
1/1 [==============================] - 0s 8ms/step


...

(15, 18) (32, 17)
-183.3664606634298
17.029386365926403
5.2849819756323315
(23, 17)
1/1 [==============================] - 0s 7ms/step
(14, 19) (31, 18)
-183.3664606634298
17.029386365926403
5.2849819756323315
(22, 18)
1/1 [==============================] - 0s 7ms/step


100%|██████████████████████████████████████████████████████████████████████████████▉| 1023/1024 [01:36<00:00, 11.92it/s]

1/1 [==============================] - 0s 7ms/step


100%|███████████████████████████████████████████████████████████████████████████████| 1024/1024 [01:36<00:00, 10.59it/s]

(16, 17) (32, 12)
-197.35402463626133
16.76305461424021
5.368949876447043
(24, 14)


In [102]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/3sad'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                          | 0/1247 [00:00<?, ?it/s]

1/1 [==============================] - 0s 8ms/step
(16, 19) (34, 21)
-173.65980825409008
18.110770276274835
4.969418673368095
(25, 20)


  0%|                                                                                  | 1/1247 [00:00<02:05,  9.91it/s]

1/1 [==============================] - 0s 8ms/step


...

(14, 21) (31, 18)
-190.00797980144134
17.26267650163207
5.213560017271431
(22, 19)
1/1 [==============================] - 0s 10ms/step
(9, 14) (27, 16)
-173.65980825409008
18.110770276274835
4.969418673368095
(18, 15)
1/1 [==============================] - 0s 9ms/step


100%|██████████████████████████████████████████████████████████████████████████████▉| 1246/1247 [01:56<00:00,  9.59it/s]

(12, 15) (33, 13)
-185.4403320310055
21.095023109728988
4.266409168259796
(22, 14)
1/1 [==============================] - 0s 9ms/step


100%|███████████████████████████████████████████████████████████████████████████████| 1247/1247 [01:56<00:00, 10.72it/s]

(14, 18) (35, 19)
-177.27368900609375
21.02379604162864
4.280863447390447
(24, 18)


In [101]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/4happy'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                          | 0/1774 [00:00<?, ?it/s]

1/1 [==============================] - 0s 9ms/step


  0%|                                                                                  | 1/1774 [00:00<04:47,  6.16it/s]

(20, 17) (37, 16)
-183.3664606634298
17.029386365926403
5.2849819756323315
(28, 16)
1/1 [==============================] - 0s 10ms/step


...

100%|██████████████████████████████████████████████████████████████████████████████▊| 1771/1774 [02:50<00:00, 11.00it/s]

(15, 19) (32, 19)
-180.0
17.0
5.294117647058824
(23, 19)
1/1 [==============================] - 0s 8ms/step
(13, 19) (28, 18)
-183.81407483429035
15.033296378372908
5.986710947139655
(20, 18)
1/1 [==============================] - 0s 8ms/step


100%|██████████████████████████████████████████████████████████████████████████████▉| 1773/1774 [02:50<00:00, 10.82it/s]

(9, 20) (24, 17)
-191.3099324740202
15.297058540778355
5.883484054145522
(16, 18)
1/1 [==============================] - 0s 8ms/step


100%|███████████████████████████████████████████████████████████████████████████████| 1774/1774 [02:50<00:00, 10.42it/s]


In [98]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/5surprise'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                           | 0/831 [00:00<?, ?it/s]

1/1 [==============================] - 0s 10ms/step


  0%|                                                                                   | 1/831 [00:00<04:00,  3.45it/s]

(16, 18) (27, 17)
-185.19442890773482
11.045361017187261
8.148217143826669
(21, 17)
1/1 [==============================] - 0s 9ms/step


...

100%|████████████████████████████████████████████████████████████████████████████████▋| 828/831 [01:19<00:00, 10.77it/s]

1/1 [==============================] - 0s 9ms/step
(12, 19) (33, 18)
-182.72631099390625
21.02379604162864
4.280863447390447
(22, 18)
1/1 [==============================] - 0s 9ms/step
(13, 18) (32, 19)
-176.98721249581666
19.026297590440446
4.730294981048731
(22, 18)


100%|████████████████████████████████████████████████████████████████████████████████▉| 830/831 [01:19<00:00, 10.52it/s]

1/1 [==============================] - 0s 8ms/step
(12, 18) (32, 18)
-180.0
20.0
4.500000000000001
(22, 18)


100%|█████████████████████████████████████████████████████████████████████████████████| 831/831 [01:19<00:00, 10.41it/s]


In [103]:
import os
import cv2

input_dir = '/storage/ali/FER/FER_code/new/test/6neutral'
output_dir = '/storage/ali/FER/FER_code/aligntest'

print(output_dir)

for root, dirs, files in os.walk(input_dir):
    
    for file in tqdm(files):
        # Create output directory
        output_dir_path = os.path.join(output_dir, os.path.split(os.path.dirname(os.path.join(root, file)))[-1])
        if not os.path.exists(output_dir_path):
            os.makedirs(output_dir_path)

        # Do preprocessing image
        img = cv2.imread(os.path.join(root, file))
        result = detector1.detect_faces(img)
        if result != []:
            for person in result:
                bounding_box = person['box']
                keypoints = person['keypoints']
                confidance = str(round(person['confidence'] * 100, 2))+"%"

                box_x,box_y=bounding_box[0], bounding_box[1]#top corner of box
                box_x1,box_y1=bounding_box[0]+bounding_box[2], bounding_box[1] + bounding_box[3]
                #cv2.rectangle(frame, (box_x,box_y), (box_x1,box_y1), (0,155,255), 2)


                #face_align(img,leye,reye,nose,desiredFaceWidth,desiredFaceHeight)
                frame=face_align(img,(keypoints['left_eye']),(keypoints['right_eye']),
                                 300,300)
        
        

        # Save it to the output directory
        cv2.imwrite(os.path.join(output_dir_path, file), frame) 

/storage/ali/FER/FER_code/aligntest


  0%|                                                                                          | 0/1233 [00:00<?, ?it/s]

1/1 [==============================] - 0s 9ms/step


  0%|                                                                                  | 1/1233 [00:00<02:26,  8.41it/s]

(13, 10) (35, 12)
-174.80557109226518
22.090722034374522
4.074108571913334
(24, 11)
1/1 [==============================] - 0s 9ms/step


...

(23, 11) (34, 15)
-160.01689347810003
11.704699910719626
7.689218919450849
(28, 13)
1/1 [==============================] - 0s 10ms/step


100%|██████████████████████████████████████████████████████████████████████████████▉| 1232/1233 [01:59<00:00,  9.83it/s]

(15, 18) (32, 21)
-169.99202019855866
17.26267650163207
5.213560017271431
(23, 19)
1/1 [==============================] - 0s 9ms/step


100%|███████████████████████████████████████████████████████████████████████████████| 1233/1233 [01:59<00:00, 10.28it/s]

(20, 21) (33, 20)
-184.39870535499554
13.038404810405298
6.902684899626334
(26, 20)
